Link Video: https://youtu.be/qhoTb9iIIqw

Saya akan meng-import data saya melalui google drive.

In [ ]:
from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


# Library

Saya akan meng-import seluruh library yang nantinya akan saya gunakan.

In [ ]:
import re
import pandas as pd
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.naive_bayes import MultinomialNB
from sklearn.svm import SVC
from sklearn.metrics import classification_report
from sklearn.metrics import f1_score
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_score
from sklearn.metrics import recall_score

# Data

Sekarang, saya akan import data ke suatu dataframe.

In [ ]:
df = pd.read_csv('/content/gdrive/MyDrive/BINUS/UAS/data_1B.csv')

In [ ]:
df.head()

Unnamed: 0                                               text  \
0           0  AV2 Women Maternity Wear/Feedind/Nursing Top &...   
1           1  Houskipper Professional Spray Mop with Best 36...   
2           2  Tat-Sat Ceramic Fondue Burner , Black This Fon...   
3           3  Prestige Plastic Hand Blender, Orange Save tim...   
4           4  Gorilla Renesa+ Energy Saving 5 Star Rated Cei...   

                    label  
0  Clothing & Accessories  
1               Household  
2               Household  
3               Household  
4               Household

Nampaknya, dataset tersebut memiliki kolom indeks karena indeks ikut terbaca sebagai kolom. Jadi, akan saya hapus kolom tersebut karena tidak diperlukan.

In [ ]:
df.drop('Unnamed: 0', axis = 1, inplace = True)

In [ ]:
df.head()

text                   label
0  AV2 Women Maternity Wear/Feedind/Nursing Top &...  Clothing & Accessories
1  Houskipper Professional Spray Mop with Best 36...               Household
2  Tat-Sat Ceramic Fondue Burner , Black This Fon...               Household
3  Prestige Plastic Hand Blender, Orange Save tim...               Household
4  Gorilla Renesa+ Energy Saving 5 Star Rated Cei...               Household

Saya akan mengecek jumlah masing-masing label.

In [ ]:
df['label'].value_counts()

Household                 4810
Books                     2946
Electronics               2693
Clothing & Accessories    2157
Name: label, dtype: int64

Saya akan mengecek seluruh isi teks pada dataset.

In [ ]:
for text in df['text']:
  print(text)

AV2 Women Maternity Wear/Feedind/Nursing Top & Capri Set Relax in these printed nightwear capri set for women from AV2. Perfect solution to your essential needs! This feeding top and capri set is perfect for day wear, casual wear. Top is printed with a graphic print , has discreet vertical zipper for your maternity and nursing use. Printed capri is comfortable and has elaticated waist with drawstring for convinience and also has a side pocket. This maternity nursing set is made with soft knitted cotton fabric.
Houskipper Professional Spray Mop with Best 360 Degree Easy Floor Cleaning for Home, Wet & Dry "Houskipper quick & easy 360 floor cleaning aluminium spray mop is made of light weight material and 360 degree wide rotating head for easy and comfortable cleaning. (1) Microfiber cleaning pad picks up 50% more dirt and dust per swipe than traditional mops. (2) Reusable, machine washable and eco-friendly microfiber mop head. (3) Safe to use on all floor types including hardwood, vinyl,

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Jannon Black Color Denim Jeans for Women This jeans from the house of Jannon is finely tailored and constructed using denim material in black color. It has skinny leg style with buttoned closure type and regular waist style. Wear this jeans during casual occasion for an elite look.
Lifestyle-You™ Height Increasing Shoes Insoles(6 cm) 3 Layers. Unisex for Male or Female One Pair of Insoles, Three layers Height increasing Insoles with total elevation of 6 Cms (2.5 Inches Appx.). You can use one , two or three layers together as per your requirement and occasion. Comes with air cushion for extra comfort. Fits shoes of all sizes. One pack contains a pair. Please see the pictures for more information about the item.
Scrafts 3" Mint Highly Fragranced/Scented Exotic Aroma Natural Wax Small Glass Jar Candle for Home Décor/Gifts/Spa/Meditation. Color:Mint   Enjoy the warmth of Aroma with this candle from Scrafts. Made from pure ingredients and essential oils, this candle ensures complete safety

Dapat kita lihat bahwa teks ini perlu dibersihkan. Teks di atas terdapat simbol-simbol yang harus dihilangkan.

# Cleaning Text

Saya akan membuat function yang bertujuan untuk membersihkan seluruh teks pada dataset.

In [ ]:
def cleaning_text(text):
  text = re.sub(r'https?\S+', '', text)
  text = re.sub(r'\S+\.com', '', text)
  text = re.sub(r'#\S+', '', text)
  text = text.replace('.', ' ')
  text = re.sub(r'[^\w\s]', ' ', text)
  text = text.replace('\n', ' ').replace('\r', ' ')
  text = re.sub(r'\s+', ' ', text.lower()).strip()

  return text

Kemudian, kita apply function tersebut pada seluruh teks pada dataset.

In [ ]:
df['text'] = df['text'].apply(lambda x: cleaning_text(x))

# Preprocessing Text

Saya akan mendownload `wordnet`, `punkt`, dan `stopwords` agar dapat melakukan preprocessing data.

In [ ]:
nltk.download('wordnet')
nltk.download('punkt')
nltk.download('stopwords')

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


True

Sekarang kita akan menginisialisasi stopwrods dan lemmatizer yang akan digunakan dalam preprocessing data. Stopwords akan diinisialisasi dengan stopwords berbahasa inggris, sedangkan lemmatizer akan menggunakan wordnet.

In [ ]:
stopwords = set(stopwords.words('english'))
lemmatizer = WordNetLemmatizer()

Saat preprocessing data, saya akan melakukan tokenisasi teks, kemudian menghilangkan seluruh stopwords pada teks, serta melakukan lemmatisasi teks. Hal ini bertujuan untuk meningkatkan performa dari model nanti dengan memberikan kata-kata dasar yang penting dalam prediksi topik. Sekarang, saya akan membuat suatu function yang bertujuan melakukan preprocessing data.

In [ ]:
def preprocessing_text(text):
  tokens = word_tokenize(text)

  without_stopword_tokens = [token for token in tokens if token.lower() not in stopwords]

  lemmatized_tokens = [lemmatizer.lemmatize(token) for token in without_stopword_tokens]

  preprocessed_text = ' '.join(lemmatized_tokens)

  return preprocessed_text

Kemudian, kita apply function tersebut pada seluruh teks pada dataset.

In [ ]:
df['text'] = df['text'].apply(lambda x: preprocessing_text(x))

Saya akan mengecek seluruh isi teks pada dataset.

In [ ]:
for text in df['text']:
  print(text)

av2 women maternity wear feedind nursing top capri set relax in these printed nightwear capri set for women from av2 perfect solution to your essential needs this feeding top and capri set is perfect for day wear casual wear top is printed with a graphic print has discreet vertical zipper for your maternity and nursing use printed capri is comfortable and has elaticated waist with drawstring for convinience and also has a side pocket this maternity nursing set is made with soft knitted cotton fabric
houskipper professional spray mop with best 360 degree easy floor cleaning for home wet dry houskipper quick easy 360 floor cleaning aluminium spray mop is made of light weight material and 360 degree wide rotating head for easy and comfortable cleaning 1 microfiber cleaning pad picks up 50 more dirt and dust per swipe than traditional mops 2 reusable machine washable and eco friendly microfiber mop head 3 safe to use on all floor types including hardwood vinyl laminate tile and many more 4

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



mototech scrambler air motorcycle jacket combo colors orange flo green grey red blue mototech scrambler air motorcycle jacket is the ideal all season mesh jacket featuring almost everything that a rider needs this jacket comes with 2 separate detachable liners a thermal warm liner and a tape seamed rain liner the mototech scrambler air jacket with ce certified armours is your perfect companion during city commutes as well as it is just what you need for long distance touring features ce shoulder and elbow armours en 1621 level 1 certified 3 in 1 all season mesh protective riding jacket with dual detachable multi weather liners reflective branding on front and back for high visibility soft back protector eva foam insert waist strap and cuff fastener for ideal fit aesthetic mototech branded puller on the main zipper fore arm button with v elastic and upper arm fastener to ensure snug fit all armours are removable internal pocket on the main jacket as well as on both the liners for conven

Dapat kita lihat bahwa teks ini telah berhasil di-preprocesing.

In [ ]:
# # Simpan DataFrame ke file CSV
# df.to_csv('cleaned_data_1B.csv', index = False)

In [ ]:
# # Download file CSV
# from google.colab import files
# files.download('cleaned_data_1B.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# Splitting Data

In [ ]:
df.head()

text                   label
0  av2 woman maternity wear feedind nursing top c...  Clothing & Accessories
1  houskipper professional spray mop best 360 deg...               Household
2  tat sat ceramic fondue burner black fondue bur...               Household
3  prestige plastic hand blender orange save time...               Household
4  gorilla renesa energy saving 5 star rated ceil...               Household

Dari dataframe di atas, terdapat hanya 2 kolom saja, yaitu `text` dan `label`. Saat ini, saya akan memisahkan data menjadi 80% training dataset dan 20% testing dataset. Untuk variabelnya sendiri, `text` akan menjadi variabel X, dan `label` akan menjadi variabel y sebagai variabel yang akan diprediksi.

In [ ]:
X = df['text']
y = df['label']

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2, random_state = 42)

In [ ]:
print(X_train[:5])

6934     bharatanatyam indian classical dance series in...
5992     micromax canavas plex tab tablet 8 inch 32gb w...
10798    leeonzi plastic toothpaste dispenser automatic...
7942     aristo multipurpose 4 drawer plastic modular c...
9246                                         touching void
Name: text, dtype: object


In [ ]:
print(X_test[:5])

8466    united color benetton boy slim fit jean ucb bo...
1399    jk steel stainless steel deluxe sev sancha jal...
4635    theory counseling psychotherapy video enhanced...
6641    generic 1 piece cash coin register insert tray...
3921    ramakada make cosmetic set suitcase durable ki...
Name: text, dtype: object


In [ ]:
print(y_train[:5])

6934           Books
5992     Electronics
10798      Household
7942       Household
9246           Books
Name: label, dtype: object


In [ ]:
print(y_test[:5])

8466    Clothing & Accessories
1399                 Household
4635                     Books
6641                 Household
3921                 Household
Name: label, dtype: object


Dapat kita lihat di atas, bahwa dataset telah berhasil dipisahkan dengan baik.

# Vectorization

Sekarang, saya akan melakukan vectorization yang bertujuan untuk mengubah bentuk data teks yang berupa string menjadi dalam bentuk vektor yang berupa numerik agar dapat diproses oleh model serta informasi yang diberikan kepada model lebih informatif sehingga meningkatkan kinerja model.

Pada umumnya, vectorizer yang sering digunakan dalam memproses data teks adalah count vectorizer dan TF-IDF vectorizer dimana kedua vectorizer tersebut memiliki cara kerja yang berbeda-beda. Saya akan membahas hal tersebut lebih lanjut di penjelasan berikutnya.

## Count Vectorizer

Saya akan menggunakan count vectorizer sebagai vectorizernya terlebih dahulu. Cara kerja count vectorizer adalah menghitung frekuensi kemunculan kata-kata dalam suatu dokumen.

Fit hanya diberlakukan kepada data training supaya vectorizernya dapat mempelajari kosakata dan menghasilkan vektor yang sesuai dengan data training. Kemudian, menggunakan transform, untuk mengubah data training dan data testing menjadi vektor yang telah dipelajari saat fit data training agar kedua vektor diubah dengan konsistensi yang sama serta mencegah terjadinya ketidakcocokan dari kedua vektor tersebut.

In [ ]:
count_vectorizer = CountVectorizer()
X_train_countVector = count_vectorizer.fit_transform(X_train)
X_test_countVector = count_vectorizer.transform(X_test)

In [ ]:
print(X_train_countVector.toarray())

[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 1 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]


In [ ]:
print(X_test_countVector.toarray())

[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]


## TF-IDF Vectorizer

Kemudian, saya akan menggunakan TF-IDF vectorizer sebagai vectorizernya. Cara kerja count vectorizer adalah menggabungkan informasi tentang frekuensi kemunculan kata dalam dokumen dengan bobot yang mengukur pentingnya kata dalam dokumen.

Fit juga hanya diberlakukan untuk training data dan transform untuk training data dan juga testing data. Tujuannya telah dijelaskan sebelumnya.


In [ ]:
tfidf_vectorizer = TfidfVectorizer()
X_train_tfidfVector = tfidf_vectorizer.fit_transform(X_train)
X_test_tfidfVector = tfidf_vectorizer.transform(X_test)

In [ ]:
print(X_train_tfidfVector.toarray())

[[0.         0.         0.         ... 0.         0.         0.        ]
 [0.         0.         0.         ... 0.         0.         0.        ]
 [0.         0.         0.         ... 0.         0.         0.        ]
 ...
 [0.         0.04833224 0.         ... 0.         0.         0.        ]
 [0.         0.         0.         ... 0.         0.         0.        ]
 [0.         0.         0.         ... 0.         0.         0.        ]]


In [ ]:
print(X_test_tfidfVector.toarray())

[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]


# Classification with Machine Learning Model



Pada soal diminta untuk melakukan pemodelan maching learning, sehingga saya akan memilih dua jenis model, yaitu model Naive Bayes dan model Support Vector Machine (SVM). Saya menggunakan kedua model tersebut, karena kedua model tersebut dapat mengatasi dengan baik akan masalah klasifikasi teks.

## Naive Bayes

Saya akan menginisialisasi model naive bayes.

In [ ]:
naiveBayes_model = MultinomialNB()

### Naive Bayes Using Count Vectorizer

Saya akan mencoba menggunakan vektor teks dari count vectorizer terlebih dahulu untuk model naive bayes.

In [ ]:
naiveBayes_model.fit(X_train_countVector, y_train)

y_naiveBayes_pred = naiveBayes_model.predict(X_test_countVector)

In [ ]:
print(classification_report(y_test, y_naiveBayes_pred))

                        precision    recall  f1-score   support

                 Books       0.98      0.89      0.94       568
Clothing & Accessories       0.94      0.98      0.96       451
           Electronics       0.91      0.93      0.92       538
             Household       0.93      0.95      0.94       965

              accuracy                           0.94      2522
             macro avg       0.94      0.94      0.94      2522
          weighted avg       0.94      0.94      0.94      2522



In [ ]:
print(f'Accuracy Score: {accuracy_score(y_test, y_naiveBayes_pred)}\n')
print(f'F1 Score: {f1_score(y_test, y_naiveBayes_pred, average = "weighted")}\n')
print(f'Precision Score: {precision_score(y_test, y_naiveBayes_pred, average = "weighted")}\n')
print(f'Recall Score: {recall_score(y_test, y_naiveBayes_pred, average = "weighted")}')

Accuracy Score: 0.93695479777954

F1 Score: 0.9369164720431762

Precision Score: 0.9380178225697262

Recall Score: 0.93695479777954


Berdasarkan hasil classification report di atas, dapat diambil kesimpulan bahwa:
- Akurasi model dan nilai F1-Score adalah 94% yang menunjukkan bahwa model naive bayes dapat memprediksi label dengan baik.
- Rata-rata nilai precision adalah 94% yang menunjukkan bahwa model naive bayes dapat memprediksi data positif dengan akurasi tinggi.
- Rata-rata nilai recall adalah 94% yang menunjukkan bahwa model naive bayes dapat mengidentifikasi dan menemukan sebagian besar data yang sebenarnya positif.

### Naive Bayes Using TF-IDF Vectorizer

Kemudian, saya akan mencoba menggunakan vektor teks dari TF-IDF vectorizer untuk model naive bayes.

In [ ]:
naiveBayes_model.fit(X_train_tfidfVector, y_train)

y_naiveBayes_pred = naiveBayes_model.predict(X_test_tfidfVector)

In [ ]:
print(classification_report(y_test, y_naiveBayes_pred))

                        precision    recall  f1-score   support

                 Books       0.99      0.88      0.93       568
Clothing & Accessories       0.98      0.88      0.93       451
           Electronics       0.96      0.87      0.91       538
             Household       0.84      0.98      0.91       965

              accuracy                           0.92      2522
             macro avg       0.94      0.90      0.92      2522
          weighted avg       0.92      0.92      0.92      2522



In [ ]:
print(f'Accuracy Score: {accuracy_score(y_test, y_naiveBayes_pred)}\n')
print(f'F1 Score: {f1_score(y_test, y_naiveBayes_pred, average = "weighted")}\n')
print(f'Precision Score: {precision_score(y_test, y_naiveBayes_pred, average = "weighted")}\n')
print(f'Recall Score: {recall_score(y_test, y_naiveBayes_pred, average = "weighted")}')

Accuracy Score: 0.9151467089611419

F1 Score: 0.915675147675569

Precision Score: 0.9232374079060597

Recall Score: 0.9151467089611419


Berdasarkan hasil classification report di atas, dapat diambil kesimpulan bahwa:
- Akurasi model dan nilai F1-Score adalah 92% yang menunjukkan bahwa model naive bayes dapat memprediksi label dengan baik.
- Rata-rata nilai precision adalah 92% yang menunjukkan bahwa model naive bayes dapat memprediksi data positif dengan akurasi tinggi.
- Rata-rata nilai recall adalah 92% yang menunjukkan bahwa model naive bayes dapat mengidentifikasi dan menemukan sebagian besar data yang sebenarnya positif.

## Support Vector Machines (SVM)

Saya akan menginisialisasi model naive bayes.

In [ ]:
svm_model = SVC()

### SVM Using Count Vectorizer

Saya akan mencoba menggunakan vektor teks dari count vectorizer terlebih dahulu untuk model SVM.

In [ ]:
svm_model.fit(X_train_countVector, y_train)

y_svm_pred = svm_model.predict(X_test_countVector)

In [ ]:
print(classification_report(y_test, y_svm_pred))

                        precision    recall  f1-score   support

                 Books       0.87      0.94      0.90       568
Clothing & Accessories       0.95      0.92      0.94       451
           Electronics       0.95      0.87      0.91       538
             Household       0.92      0.93      0.92       965

              accuracy                           0.92      2522
             macro avg       0.92      0.92      0.92      2522
          weighted avg       0.92      0.92      0.92      2522



In [ ]:
print(f'Accuracy Score: {accuracy_score(y_test, y_svm_pred)}\n')
print(f'F1 Score: {f1_score(y_test, y_svm_pred, average = "weighted")}\n')
print(f'Precision Score: {precision_score(y_test, y_svm_pred, average = "weighted")}\n')
print(f'Recall Score: {recall_score(y_test, y_svm_pred, average = "weighted")}')

Accuracy Score: 0.9183187946074544

F1 Score: 0.9184065831802438

Precision Score: 0.920088689422291

Recall Score: 0.9183187946074544


Berdasarkan hasil classification report di atas, dapat diambil kesimpulan bahwa:
- Akurasi model dan nilai F1-Score adalah 92% yang menunjukkan bahwa model SVM dapat memprediksi label dengan baik.
- Rata-rata nilai precision adalah 92% yang menunjukkan bahwa model SVM dapat memprediksi data positif dengan akurasi tinggi.
- Rata-rata nilai recall adalah 92% yang menunjukkan bahwa model SVM dapat mengidentifikasi dan menemukan sebagian besar data yang sebenarnya positif.

### SVM Using TF-IDF Vectorizer

Kemudian, saya akan mencoba menggunakan vektor teks dari TF-IDF vectorizer untuk model SVM.

In [ ]:
svm_model.fit(X_train_tfidfVector, y_train)

y_svm_pred = svm_model.predict(X_test_tfidfVector)

In [ ]:
print(classification_report(y_test, y_svm_pred))

                        precision    recall  f1-score   support

                 Books       0.98      0.93      0.95       568
Clothing & Accessories       0.98      0.97      0.97       451
           Electronics       0.96      0.93      0.94       538
             Household       0.93      0.98      0.95       965

              accuracy                           0.95      2522
             macro avg       0.96      0.95      0.95      2522
          weighted avg       0.95      0.95      0.95      2522



In [ ]:
print(f'Accuracy Score: {accuracy_score(y_test, y_svm_pred)}\n')
print(f'F1 Score: {f1_score(y_test, y_svm_pred, average = "weighted")}\n')
print(f'Precision Score: {precision_score(y_test, y_svm_pred, average = "weighted")}\n')
print(f'Recall Score: {recall_score(y_test, y_svm_pred, average = "weighted")}')

Accuracy Score: 0.9536082474226805

F1 Score: 0.9535750115762321

Precision Score: 0.9543611659640248

Recall Score: 0.9536082474226805


Berdasarkan hasil classification report di atas, dapat diambil kesimpulan bahwa:
- Akurasi model dan nilai F1-Score adalah 95% yang menunjukkan bahwa model SVM dapat memprediksi label dengan baik.
- Rata-rata nilai precision adalah 95% yang menunjukkan bahwa model SVM dapat memprediksi data positif dengan akurasi tinggi.
- Rata-rata nilai recall adalah 95% yang menunjukkan bahwa model SVM dapat mengidentifikasi dan menemukan sebagian besar data yang sebenarnya positif.

Berdasarkan hasil analisa classification report, dapat kita ketahui bahwa baik model naive bayes dan model SVM sama-sama memiliki akurasi yang tinggi dalam mengatasi permasalah klasifikasi teks deskripsi produk e-commerce. Namun, untuk dapat kita perhatikan bahwa ada perbedaan akurasi pada kedua model.

Untuk model naive bayes, tingkat akurasi menjadi sedikit lebih tinggi jika menggunakan Count Vectorizer. Sedangkan, untuk model SVM, tingkat akurasi menjadi sedikit lebih tinggi jika menggunakan TF-IDF Vectorizer.

Jika kita bandingkan berdasarkan tingkat akurasinya, model SVM yang menggunakan TF-IDF Vectorizer adalah model terbaik untuk klasifikasi teks deskripsi produk e-commerce.